In [9]:
# hidden
import environment as env
env.initialize()

### Pretatamiento de las series temporales de los agentes climáticos marítimos y atmosféricos

Este ejemplo continuará a partir de los datos temporales guardados al final del apartado [Lectura de las series temporales de los agentes climáticos marítimos y atmosféricos](cl_lectura_pretratamiento_01.ipynb). En este ejemplo se presenta el procedimiento para el relleno de huecos de los datos del punto SIMAR 1052046, proporcionado por Puertos del Estado. Se utilizan datos de la Boya del Golfo de Cádiz para completar los datos del punto SIMAR 1052046.

Las funciones que se utilizan son:

- analogos.reconstruct_analogs.input_data_analogos_rellenoh
- analogos.reconstruct_analogs.reconstruct_analogs
- analogos.reconstruct_analogs.output_data_analogos
- analogos.reconstruct_analogs.plot_reconstruct_analogos

In [10]:
# imports Anaconda
from __future__ import division
import pandas as pd
import numpy as np
import os

# imports ROM 1.1
from entrada_datos import lectura
from analogos import reconstruct_analogs
from clima_maritimo.clima_maritimo import pretratamiento_clima

dir_data = os.path.join(env.data_path, 'clima')
dir_input = os.path.join(env.input_path, 'clima')
cadiz_hs_sim = pd.read_pickle(os.path.join(dir_data, 'cadiz_hs_simc.pkl'))

En primer lugar, es necesarion realizar la lectura de los datos de altura de ola significante correspondiente a la Boya del Golfo de Cádiz. Para ello, se utiliza la función $lectura\_redcos$ del módulo $lectura$.

In [11]:
cadiz_boya = 'REDCOS_HIS_CostCadiz'
cadiz_hs_boy, cadiz_tp_boy, cadiz_dh_boy = lectura.lectura_redcos(dir_input, cadiz_boya)

Los datos correspondientes a la serie temporal de altura de ola correspondientes al punto SIMAR 1052045, que debe ser reconstruida se denominan como "predictandos" ($df\_loc$), mientras que los datos de la Boya de Cádiz corresponde al conjunto de datos "predictores" ($df\_pred$).

In [12]:
df_loc = cadiz_hs_sim
df_pred = pd.merge(cadiz_hs_boy, cadiz_tp_boy, how='inner', left_index=True, right_index=True)

Las relaciones entre ambos conjuntos de datos durante el periodo de entrenamiento ($ttrain$) son empleadas para reconstruir la serie observada durante el periodo para el cual no existen observaciones (periodo a reconstruir $trec$). Con la función $input\_data\_analogos\_rellenoh$ se identifican los datos de ambas series temporales correspondientes a los periodos de entrenamiento y reconstrucción. 

NOTA: En el caso que la serie de predictores no posea información en todos los instantes de tiempo de huecos de la serie de los predictandos, se muestra un aviso. El software permite continuar con el proceso aunque seguirán habiendo puntos en los que no sea posible realizar la reconstrucción.

In [13]:
loc_ttrain, pred_ttrain, pred_trec = reconstruct_analogs.input_data_analogos_rellenoh(df_loc, df_pred)

El dataframe de datos de los predictores no contiene suficiente informacion. Revisar los resultados de la reconstrucción


Se deben definir una serie de parámetros:

- $k$: Numero de analogos escogido para reconstruir cada instante.
- $atrend$: Tendencia temporal de los analogos (intervalo de comparacion en horas).
- $sw$: Ventana de busqueda para los candidatos a analogos en horas.
- $wp$: Vector de ponderacion de pesos para la metrica de analogos.

Tambien se debe indicar los siguientes campos:
- $esc\_pred$: Columnas de predictores correspondientes a variables escalares (empieza en 1).
- $circ\_pred$: Columnas de predictores correspondientes a variables circulares (empieza en 1).
        

In [14]:
par = {'k': 25, 'a_trend': 12, 'sw': 0, 'wp': np.array([1, 1])}
esc_pred = np.array([1, 2])
circ_pred = np.array([])

La función $reconstruct\_analogs$ permite obtener los datos correspondiente a la serie de predictandos durante el periodo de reconstrucción. A continuación la función $output\_data\_analogs$ permite la obtención de la serie final de predictandos.

NOTA: Dado que la función $reconstruct\_analogs$ conlleva una gran cantidad de tiempo de ejecución. Se han guardado los resultados de la serie reconstruida a archivo y no se ejecutan en este ejemplo. 

In [ ]:
# df_loc_trec = reconstruct_analogs.reconstruct_analogs(loc_ttrain, pred_ttrain, pred_trec, esc_pred, circ_pred, par)
# cadiz_hs_sim_reconst = reconstruct_analogs.output_data_analogos(loc_ttrain, df_loc_trec)

cadiz_hs_sim_reconst = pd.read_pickle(os.path.join(dir_data, 'cadiz_hs_reconst.pkl'))
cadiz_hs_sim.update(cadiz_hs_sim_reconst)

Por último se incluye en esta función el uso de la función:
- clima_maritimo.clima_maritimo.pretratamiento_clima.interp_distrib

Esta función permite distribuir los datos para evitar problemas en los ajustes por máxima verosimilitud usados en el análisis estadístico del clima. En esta función se debe definir el parámetro:

- umb_an: Umbral para descartar anos con menos porcentaje de numero de datos

In [ ]:
umb_an = 0.8
cadiz_hs_sim = pretratamiento_clima.interp_distrib(umb_an, cadiz_hs_sim)
cadiz_hs_sim.to_pickle(os.path.join(dir_data, 'cadiz_hs_sim_pretrat.pkl')) 

El proceso de transformación oceanográfica de estados de oleaje offshore al emplazamiento se realiza en el apartado  [Transformacion de los estados de las variables oceanograficas_al_emplazamiento](cl_transformacion_emplazamiento_01.ipynb).